In [1]:
import sys
sys.path.append('../')

# import pandas as pd
import modin.pandas as pd
import numpy as np
import math
from timeit import default_timer as timer
from datetime import datetime, timedelta
import numba
import joblib 


/Users/neilkloot/anaconda/lib/python3.6/site-packages/numba/errors.py:137: UserWarning: Insufficiently recent colorama version found. Numba requires colorama >= 0.3.9
  warnings.warn(msg)


In [2]:
pd.options.display.max_rows=500
pd.options.display.max_columns=500
%load_ext autoreload
%autoreload 2


In [3]:
def load(filename):
    """Loads a compressed object from disk
    """
    model_object = joblib.load(filename)
    return model_object


In [4]:
all_df = pd.read_pickle('../data/ml-ta-all-data-201908262001.pkl.gz', compression='gzip')
print('Data loaded')
print(all_df.shape)

Data loaded
(1079523, 1227)


In [5]:
from optimise_dataframe import optimise_df

all_df = optimise_df(all_df)
train_df = all_df

In [6]:
del all_df

In [7]:
target_col = 'target'

numeric_cols = []
category_cols = []

for col in train_df.columns:
    if train_df[col].dtype.name == 'object':
        print(col, train_df[col].dtype.name)
    elif train_df[col].dtype.name == 'category' and col != target_col:
        category_cols.append(col)
        print('category:', col)
    elif train_df[col].dtype.name != 'int8' and col != target_col:
        numeric_cols.append(col)
    elif col == target_col:
        print('--- Target', col, train_df[col].dtype.name)

# print(numeric_cols)


category: one_week_bollinger_prediction
category: two_week_bollinger_prediction
category: four_week_bollinger_prediction
category: eight_week_bollinger_prediction
category: twelve_week_bollinger_prediction
category: twenty_six_week_bollinger_prediction
category: fifty_two_week_bollinger_prediction
category: one_week_bollinger_type
category: two_week_bollinger_type
category: four_week_bollinger_type
category: eight_week_bollinger_type
category: twelve_week_bollinger_type
category: twenty_six_week_bollinger_type
category: fifty_two_week_bollinger_type
category: symbol
category: GICSSector
category: GICSIndustryGroup
category: GICSIndustry
--- Target target float32


In [58]:
# Split data for train / test 
groups = train_df.groupby('symbol')

train_data = pd.DataFrame(groups.apply(lambda x: x.sample(frac=0.9)))
test_data = train_df.set_index(['symbol', 'week_starting']).drop(train_data.index)
test_data['symbol'] = test_data.index.get_level_values(0)

print(train_df.shape)
print(train_data.shape)
print(test_data.shape)


(1079523, 1228)
(971418, 1228)
(108105, 1226)


In [59]:
from sklearn import preprocessing

# Scale all numeric columns excluding target col
print('Scaling', len(numeric_cols), 'of', train_data.shape[1], 'cols')

scaler = preprocessing.MinMaxScaler()

# Fill any infinities, -infinites, NaNs which will cause scaler to fail
train_data.replace([np.inf, -np.inf], np.nan, inplace=True)
train_data[numeric_cols] = train_data[numeric_cols].fillna(0)

test_data.replace([np.inf, -np.inf], np.nan, inplace=True)
test_data[numeric_cols] = test_data[numeric_cols].fillna(0)

# Transform data and fill any NAs
scaler.fit(train_data[numeric_cols])
train_data[numeric_cols] = scaler.transform(train_data[numeric_cols])
train_data[numeric_cols] = train_data[numeric_cols].fillna(0)

test_data[numeric_cols] = scaler.transform(test_data[numeric_cols])
test_data[numeric_cols] = test_data[numeric_cols].fillna(0)


joblib.dump(scaler, '../models/scaler.joblib.z') 


Scaling 1007 of 1228 cols


/Users/neilkloot/anaconda/lib/python3.6/site-packages/sklearn/preprocessing/data.py:323: DataConversionWarning: Data with input dtype float32 were all converted to float64 by MinMaxScaler.
  return self.partial_fit(X, y)


['../models/scaler.joblib.z']

In [60]:
train_data[numeric_cols].head(100)

lastTradePriceOnly  adjustedPrice    volume  \
symbol week_starting                                                
14D    2019-01-06               0.000831       0.020204  0.000100   
       2019-01-20               0.000789       0.020202  0.000148   
       2018-12-23               0.000817       0.020203  0.000204   
       2019-01-13               0.000803       0.020203  0.000146   
       2018-11-18               0.000734       0.020201  0.000401   
       2019-02-17               0.001011       0.020209  0.000484   
       2018-11-11               0.000789       0.020202  0.000295   
       2018-09-16               0.000817       0.020203  0.013578   
       2018-12-09               0.000706       0.020200  0.000215   
       2018-12-02               0.000734       0.020201  0.000176   
       2018-11-04               0.000803       0.020203  0.000349   
       2019-02-10               0.001080       0.020211  0.000640   
       2019-01-27               0.000845       0.020204  0.000418   
       2018-10-07               0.000969       0.020207  0.001267   
       2018-12-16               0.000734       0.020201  0.000400   
       2018-11-25               0.000734       0.020201  0.000242   
       2019-02-24               0.001011       0.020209  0.000273   
       2018-10-21               0.000859       0.020204  0.000967   
       2018-12-30               0.000803       0.020203  0.000172   
       2018-09-23               0.001039       0.020210  0.018283   
       2018-10-28               0.000817       0.020203  0.000446   
       2018-10-14               0.000845       0.020204  0.001382   
1AD    2018-05-20               0.000838       0.020204  0.000000   
       2018-04-01               0.000942       0.020207  0.000000   
       2017-07-30               0.000637       0.020198  0.000067   
       2017-02-12               0.000637       0.020198  0.000000   
       2018-12-23               0.000651       0.020198  0.000134   
       2017-02-19               0.000568       0.020196  0.000000   
       2018-12-09               0.000692       0.020199  0.000014   
       2017-09-03               0.000609       0.020197  0.000058   
       2017-04-16               0.000699       0.020199  0.000635   
       2018-08-12               0.000831       0.020204  0.000024   
       2016-11-20               0.000568       0.020198  0.000000   
       2018-10-28               0.000775       0.020202  0.000000   
       2018-10-07               0.000803       0.020201  0.000000   
       2017-04-02               0.000609       0.020197  0.000041   
       2018-04-08               0.000817       0.020207  0.000000   
       2016-10-16               0.000595       0.020197  0.000067   
       2018-06-03               0.000955       0.020207  0.000000   
       2018-12-16               0.000623       0.020198  0.000000   
       2017-07-23               0.000623       0.020198  0.000023   
       2019-01-27               0.000706       0.020198  0.000000   
       2018-09-23               0.000775       0.020202  0.000000   
       2017-03-26               0.000637       0.020198  0.000007   
       2019-01-06               0.000665       0.020198  0.000000   
       2017-10-22               0.000000       0.020198  0.000000   
       2016-09-11               0.000609       0.020197  0.000251   
       2016-10-30               0.000561       0.020195  0.000151   
       2018-11-25               0.000775       0.020201  0.000012   
       2019-01-20               0.000665       0.020198  0.000000   
       2018-01-14               0.000713       0.020200  0.000100   
       2018-06-10               0.000942       0.020208  0.000150   
       2018-03-25               0.000942       0.020207  0.000002   
       2017-09-17               0.000000       0.020197  0.000000   
       2018-06-24               0.000997       0.020209  0.000145   
       2016-09-18               0.000692       0.020199  0.000342   
       2016-08-28   

In [75]:
test_data[numeric_cols].head(100)

lastTradePriceOnly  adjustedPrice        volume  \
symbol week_starting                                                    
AFR    2007-07-08               0.002089       0.020241  9.435377e-05   
GXY    2007-07-08               0.001994       0.020239  4.023059e-04   
MRM    2007-07-08               0.004861       0.020272  5.348643e-04   
ASX    2007-07-08               0.133546       0.022472  1.289694e-03   
FSE    2007-07-08               0.000216       0.020185  1.114156e-02   
LTR    2007-07-08               0.000680       0.020195  7.409376e-04   
SGO    2007-07-08               0.000068       0.020193  3.675745e-05   
BDM    2007-07-08               0.000720       0.020200  1.157715e-05   
ALL    2007-07-08               0.039188       0.021051  7.088399e-03   
CND    2007-07-08               0.008998       0.020278  1.447144e-04   
LEP    2007-07-08               0.011909       0.020307  3.623648e-04   
GED    2007-07-08               0.000277       0.020187  0.000000e+00   
ACG    2007-07-08               0.000401       0.020190  8.248719e-06   
PMC    2007-07-08               0.005733       0.020353  4.396423e-04   
ATR    2007-07-08               0.007533       0.020272  3.791516e-05   
LLC    2007-07-08               0.050674       0.021036  3.791806e-03   
IAM    2007-07-08               0.000075       0.020217  1.956538e-04   
SRX    2007-07-08               0.009693       0.020434  8.075062e-05   
SAR    2007-07-08               0.001146       0.020213  5.409423e-04   
AEI    2007-07-08               0.001322       0.020219  0.000000e+00   
EVE    2007-07-08               0.000384       0.020190  3.548975e-03   
GUL    2007-07-08               0.000244       0.020186  2.228601e-05   
ZNC    2007-07-08               0.001036       0.020210  2.043367e-04   
KGM    2007-07-08               0.002631       0.020256  1.751044e-04   
SSM    2007-07-08               0.005357       0.020282  1.356552e-03   
TDL    2007-07-08               0.011214       0.020520  5.499146e-04   
SDG    2007-07-08               0.011355       0.020417  1.841056e-03   
MBE    2007-07-08               0.000374       0.020190  4.865297e-04   
CNX    2007-07-08               0.000518       0.020194  2.278094e-03   
QRX    2007-07-08               0.004885       0.020319  6.127206e-04   
XCD    2007-07-08               0.000471       0.020322  9.261720e-06   
KIK    2007-07-08               0.000566       0.020754  8.538148e-05   
LCK    2007-07-08               0.016870       0.020665  6.737901e-04   
HII    2007-07-08               0.000997       0.020200  3.617859e-05   
ZIM    2007-07-08               0.042234       0.021212  1.360315e-05   
OGY    2007-07-08               0.000065       0.020218  1.259594e-03   
KAB    2007-07-08               0.000674       0.020193  1.415885e-03   
AIZ    2007-07-08               0.006397       0.020274  5.467309e-04   
SGU    2007-07-08               0.000199       0.020301  3.617859e-06   
ELX    2007-07-08               0.002109       0.020242  4.225660e-05   
HIG    2007-07-08               0.000512       0.020194  2.101253e-03   
SHL    2007-07-08               0.041320       0.020956  2.334243e-03   
FLK    2007-07-08               0.002409       0.020450  2.518030e-05   
CWC    2007-07-08               0.000623       0.020197  1.164951e-04   
PMV    2007-07-08               0.024233       0.020483  4.399317e-05   
SLX    2007-07-08               0.033594       0.021203  2.494876e-04   
RNY    2007-07-08               0.003199       0.020257  6.642390e-04   
COE    2007-07-08               0.002091       0.020242  2.595307e-03   
LNG    2007-07-08               0.001828       0.020234  1.649744e-04   
ANP    2007-07-08               0.000070       0.020200  4.535348e-04   
HVN    2007-07-08               0.014417       0.020418  3.605414e-03   
FXR    2007-07-08               0.002798       0.020261  5.695379e-03   
IMC    2007-07-08               0.000322       0.020553  2.894287e-07   
CDI    

In [62]:
def one_hot_encode_field(df, column_name, categories):
    new_cols = pd.get_dummies(df[column_name])
    new_cols = new_cols.astype('int8', errors='ignore')

    new_cols.T.reindex(categories).T.fillna(0)
    
    name_map = {}
    # rename the categories
    for val in categories:
        name_map[val] = val

    new_cols.rename(name_map, axis=1, inplace=True)
    
    # Remove the original column
    df.drop([column_name], axis=1, inplace=True)
    
    # Return df with new cols 
    return pd.concat([df, new_cols], axis=1)



In [63]:
from sklearn.preprocessing import LabelEncoder

def prep_class_index(df, column_name, categories):
    # Create 
    val_map = {}
    for i in range(len(categories)):
        val_map[categories[i]] = i
        
    print(val_map)
    df['class_index'] = df[column_name].map(val_map).values
    
    # Return df with new target index col
    return df


In [64]:
bins = [-99.07692719, -13.13461361, -3.00000238, 0.,9.25964718, 1493.]
bin_names = ['strong_sell', 'sell', 'hold', 'buy', 'strong_buy']


In [65]:
# prep data for training with one hot encoding
train_data['class'] = pd.cut(train_data['target'], bins=bins,labels=bin_names)
train_data = prep_class_index(train_data, 'class', bin_names)
train_data = one_hot_encode_field(train_data, 'class', bin_names)


test_data['class'] = pd.cut(test_data['target'], bins=bins,labels=bin_names)
test_data = prep_class_index(test_data, 'class', bin_names)
test_data = one_hot_encode_field(test_data, 'class', bin_names)


{'strong_sell': 0, 'sell': 1, 'hold': 2, 'buy': 3, 'strong_buy': 4}
{'strong_sell': 0, 'sell': 1, 'hold': 2, 'buy': 3, 'strong_buy': 4}


In [66]:
from keras.models import Model
from keras.layers import Input, Dense, Concatenate, Reshape, Dropout
from keras.layers.embeddings import Embedding
from keras import optimizers, initializers

# Determine unique vals for each category
col_vals_dict = {c: list(train_df[c].unique()) for c in category_cols}

embed_cols = []
for c in category_cols:
    if len(col_vals_dict[c])>2:
        embed_cols.append(c)
        print(c + ': %d values' % len(col_vals_dict[c])) #look at value counts to know the embedding dimensions

        
# Build embedding network for category cols
inputs = []
embeddings = []

initalizer = initializers.TruncatedNormal(stddev=0.00002, seed=1975)
print('Initializer:', initalizer)

for c in embed_cols:
    embedding_input = Input(shape=(1,))
    vocab_size = len(col_vals_dict[c]) + 1
    embedding_size = int(min(np.ceil(vocab_size/2), 50))
    embedding = Embedding(vocab_size, embedding_size, input_length=1)(embedding_input)
    embedding = Reshape(target_shape=(embedding_size,))(embedding)
    print('Create embedding', c, col_vals_dict[c])
    print('Embedding size', embedding_size)
    print('Vocab size', vocab_size)
    inputs.append(embedding_input)
    embeddings.append(embedding)
    
# Add embedding for numeric cols
input_numeric = Input(shape=(len(numeric_cols),))
embedding_numeric = Dense(len(numeric_cols))(input_numeric) 
inputs.append(input_numeric)
embeddings.append(embedding_numeric)
print('Create numeric embedding')
print('Input shape', (len(numeric_cols),))


# Build model
x = Concatenate()(embeddings)
x = Dense(1000, activation='relu', kernel_initializer=initalizer)(x)
x = Dropout(.4)(x)
x = Dense(500, activation='relu', kernel_initializer=initalizer)(x)
x = Dropout(.4)(x)
x = Dense(200, activation='relu', kernel_initializer=initalizer, name='int_layer')(x)
x = Dropout(.1)(x)
output = Dense(5, activation='softmax')(x)

model = Model(inputs, output)
                             
model.summary()

model.compile(loss='kullback_leibler_divergence', optimizer=optimizers.Adamax(learning_rate=0.006),
              metrics=['accuracy'])

intermediate_model = Model(inputs=model.input, outputs=model.get_layer('int_layer').output)


one_week_bollinger_prediction: 3 values
two_week_bollinger_prediction: 3 values
four_week_bollinger_prediction: 3 values
eight_week_bollinger_prediction: 3 values
twelve_week_bollinger_prediction: 3 values
twenty_six_week_bollinger_prediction: 3 values
fifty_two_week_bollinger_prediction: 3 values
one_week_bollinger_type: 3 values
two_week_bollinger_type: 3 values
four_week_bollinger_type: 3 values
eight_week_bollinger_type: 3 values
twelve_week_bollinger_type: 3 values
twenty_six_week_bollinger_type: 3 values
fifty_two_week_bollinger_type: 3 values
symbol: 2632 values
GICSSector: 13 values
GICSIndustryGroup: 26 values
GICSIndustry: 69 values
Initializer: <keras.initializers.TruncatedNormal object at 0x15855e160>
Create embedding one_week_bollinger_prediction ['Steady', 'Falling', 'Rising']
Embedding size 2
Vocab size 4
Create embedding two_week_bollinger_prediction ['Steady', 'Rising', 'Falling']
Embedding size 2
Vocab size 4
Create embedding four_week_bollinger_prediction ['Steady', 

Model: "model_11"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_96 (InputLayer)           (None, 1)            0                                            
__________________________________________________________________________________________________
input_97 (InputLayer)           (None, 1)            0                                            
__________________________________________________________________________________________________
input_98 (InputLayer)           (None, 1)            0                                            
__________________________________________________________________________________________________
input_99 (InputLayer)           (None, 1)            0                                            
___________________________________________________________________________________________

In [76]:
# Prep data for model

input_list_train = []
input_list_test = []
category_val_maps = {}

# the cols to be embedded: rescaling to range [0, # values)
for c in category_cols:
    print('Processing', c)
    # Get full set of possible vals from complete data-set
    raw_vals = np.unique(train_df[c])
    val_map = {}
    for i in range(len(raw_vals)):
        val_map[raw_vals[i]] = i       
    category_val_maps[c] = val_map
    input_list_train.append(train_data[c].map(val_map).values)

#the rest of the columns
print('Processing numeric cols')
print(train_data[numeric_cols].shape)
input_list_train.append(train_data[numeric_cols].values)

print('Train X len', len(input_list_train))
print('Train X nulls', train_data[category_cols].isnull().any().sum())

# the cols to be embedded: rescaling to range [0, # values)
for c in category_cols:
    print('Processing', c)
    val_map = category_val_maps[c]
    input_list_test.append(test_data[c].map(val_map).values)

#the rest of the columns
print('Processing numeric cols')
print(test_data[numeric_cols].shape)
input_list_test.append(test_data[numeric_cols].values)

print('Test X len', len(input_list_test))
print('Test X nulls', test_data[category_cols].isnull().any().sum())

joblib.dump(category_val_maps, '../models/category_val_maps.joblib.z') 


Processing one_week_bollinger_prediction
Processing two_week_bollinger_prediction
Processing four_week_bollinger_prediction
Processing eight_week_bollinger_prediction
Processing twelve_week_bollinger_prediction
Processing twenty_six_week_bollinger_prediction
Processing fifty_two_week_bollinger_prediction
Processing one_week_bollinger_type
Processing two_week_bollinger_type
Processing four_week_bollinger_type
Processing eight_week_bollinger_type
Processing twelve_week_bollinger_type
Processing twenty_six_week_bollinger_type
Processing fifty_two_week_bollinger_type
Processing symbol
Processing GICSSector
Processing GICSIndustryGroup
Processing GICSIndustry
Processing numeric cols
(971418, 1007)
Train X len 19
Train X nulls 0
Processing one_week_bollinger_prediction
Processing two_week_bollinger_prediction
Processing four_week_bollinger_prediction
Processing eight_week_bollinger_prediction
Processing twelve_week_bollinger_prediction
Processing twenty_six_week_bollinger_prediction
Processi

['../models/category_val_maps.joblib.z']

In [ ]:
# Set y values
y_train = train_data[bin_names].values
print('Train y shape', y_train.shape)
print('Train y nulls', train_data[bin_names].isnull().any().sum())

y_test = test_data[bin_names].values
print('Test y shape', y_test.shape)
print('Test y nulls', test_data[bin_names].isnull().any().sum())


Train y shape (971418, 5)
Train y nulls 0
Test y shape (108105, 5)
Test y nulls 0


In [ ]:
# Train model
from keras.callbacks import EarlyStopping, ReduceLROnPlateau

print('Initializer:', initalizer)

reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2, patience=5, min_lr=0.00001, verbose=1)
model.fit(input_list_train, 
          y_train, 
          validation_data=(input_list_test, y_test), 
          epochs=1000, 
          batch_size=256, 
          verbose=1, 
          callbacks=[reduce_lr]
         )

# 500, 200, 100 lr 0.004 => epoch 60: loss: 1.2622, accuracy: 0.4701, num lr reductions: 0
# 1000, 500, 200 lr 0.006 => epoch 60: loss: 1.3076, accuracy: 0.4484, num lr reductions: 0
# 1000, 500, 200 lr 0.006 => epoch 1000: loss: 1.0373 , accuracy: 0.5743, num lr reductions: max


Initializer: <keras.initializers.TruncatedNormal object at 0x15855e160>


/Users/neilkloot/anaconda/lib/python3.6/site-packages/tensorflow_core/python/framework/indexed_slices.py:424: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Train on 971418 samples, validate on 108105 samples
Epoch 1/1000
971418/971418 [==============================] - 2042s 2ms/step - loss: 1.4702 - accuracy: 0.3557 - val_loss: 1.4246 - val_accuracy: 0.3968
Epoch 2/1000
971418/971418 [==============================] - 320s 329us/step - loss: 1.4267 - accuracy: 0.3878 - val_loss: 1.4129 - val_accuracy: 0.3920
Epoch 3/1000
971418/971418 [==============================] - 322s 331us/step - loss: 1.4173 - accuracy: 0.3931 - val_loss: 1.4150 - val_accuracy: 0.3962
Epoch 4/1000
971418/971418 [==============================] - 325s 335us/step - loss: 1.4043 - accuracy: 0.4004 - val_loss: 1.3908 - val_accuracy: 0.4061
Epoch 5/1000
971418/971418 [==============================] - 325s 334us/step - loss: 1.3937 - accuracy: 0.4062 - val_loss: 1.3911 - val_accuracy: 0.3915
Epoch 6/1000
971418/971418 [==============================] - 317s 326us/step - loss: 1.3880 - accuracy: 0.4092 - val_loss: 1.3634 - val_accuracy: 0.4209
Epoch 7/1000
971418/97141

971418/971418 [==============================] - 310s 320us/step - loss: 1.2901 - accuracy: 0.4537 - val_loss: 1.3044 - val_accuracy: 0.4523
Epoch 53/1000
971418/971418 [==============================] - 310s 319us/step - loss: 1.2885 - accuracy: 0.4544 - val_loss: 1.3031 - val_accuracy: 0.4521
Epoch 54/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2884 - accuracy: 0.4545 - val_loss: 1.3044 - val_accuracy: 0.4525
Epoch 55/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2878 - accuracy: 0.4548 - val_loss: 1.3006 - val_accuracy: 0.4529
Epoch 56/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2874 - accuracy: 0.4548 - val_loss: 1.3022 - val_accuracy: 0.4531
Epoch 57/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2870 - accuracy: 0.4552 - val_loss: 1.3052 - val_accuracy: 0.4532
Epoch 58/1000
971418/971418 [==============================] - 310s 319us/step - los

Epoch 104/1000
971418/971418 [==============================] - 275s 283us/step - loss: 1.2823 - accuracy: 0.4572 - val_loss: 1.3030 - val_accuracy: 0.4536
Epoch 105/1000
971418/971418 [==============================] - 280s 288us/step - loss: 1.2830 - accuracy: 0.4568 - val_loss: 1.3029 - val_accuracy: 0.4536
Epoch 106/1000
971418/971418 [==============================] - 281s 289us/step - loss: 1.2828 - accuracy: 0.4569 - val_loss: 1.3025 - val_accuracy: 0.4538
Epoch 107/1000
971418/971418 [==============================] - 283s 291us/step - loss: 1.2830 - accuracy: 0.4572 - val_loss: 1.3028 - val_accuracy: 0.4538
Epoch 108/1000
971418/971418 [==============================] - 282s 290us/step - loss: 1.2827 - accuracy: 0.4573 - val_loss: 1.3029 - val_accuracy: 0.4537
Epoch 109/1000
971418/971418 [==============================] - 281s 290us/step - loss: 1.2830 - accuracy: 0.4569 - val_loss: 1.3027 - val_accuracy: 0.4535
Epoch 110/1000
971418/971418 [==============================] - 

971418/971418 [==============================] - 310s 319us/step - loss: 1.2820 - accuracy: 0.4574 - val_loss: 1.3026 - val_accuracy: 0.4537
Epoch 157/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2820 - accuracy: 0.4572 - val_loss: 1.3030 - val_accuracy: 0.4538
Epoch 158/1000
971418/971418 [==============================] - 310s 319us/step - loss: 1.2815 - accuracy: 0.4576 - val_loss: 1.3024 - val_accuracy: 0.4536
Epoch 159/1000
971418/971418 [==============================] - 311s 320us/step - loss: 1.2817 - accuracy: 0.4576 - val_loss: 1.3027 - val_accuracy: 0.4541
Epoch 160/1000
971418/971418 [==============================] - 311s 320us/step - loss: 1.2824 - accuracy: 0.4572 - val_loss: 1.3029 - val_accuracy: 0.4537
Epoch 161/1000
971418/971418 [==============================] - 310s 319us/step - loss: 1.2821 - accuracy: 0.4575 - val_loss: 1.3029 - val_accuracy: 0.4539
Epoch 162/1000
971418/971418 [==============================] - 310s 319us/step

971418/971418 [==============================] - 325s 334us/step - loss: 1.2817 - accuracy: 0.4573 - val_loss: 1.3017 - val_accuracy: 0.4538
Epoch 209/1000
971418/971418 [==============================] - 325s 334us/step - loss: 1.2814 - accuracy: 0.4578 - val_loss: 1.3018 - val_accuracy: 0.4540
Epoch 210/1000
971418/971418 [==============================] - 327s 336us/step - loss: 1.2811 - accuracy: 0.4575 - val_loss: 1.3019 - val_accuracy: 0.4536
Epoch 211/1000
971418/971418 [==============================] - 327s 336us/step - loss: 1.2812 - accuracy: 0.4581 - val_loss: 1.3016 - val_accuracy: 0.4541
Epoch 212/1000
971418/971418 [==============================] - 328s 337us/step - loss: 1.2810 - accuracy: 0.4573 - val_loss: 1.3016 - val_accuracy: 0.4541
Epoch 213/1000
971418/971418 [==============================] - 329s 338us/step - loss: 1.2811 - accuracy: 0.4575 - val_loss: 1.3023 - val_accuracy: 0.4540
Epoch 214/1000
971418/971418 [==============================] - 331s 340us/step

971418/971418 [==============================] - 315s 324us/step - loss: 1.2808 - accuracy: 0.4576 - val_loss: 1.3020 - val_accuracy: 0.4540
Epoch 261/1000
971418/971418 [==============================] - 315s 324us/step - loss: 1.2810 - accuracy: 0.4579 - val_loss: 1.3023 - val_accuracy: 0.4538
Epoch 262/1000
971418/971418 [==============================] - 315s 325us/step - loss: 1.2804 - accuracy: 0.4579 - val_loss: 1.3016 - val_accuracy: 0.4542
Epoch 263/1000
971418/971418 [==============================] - 315s 324us/step - loss: 1.2804 - accuracy: 0.4579 - val_loss: 1.3019 - val_accuracy: 0.4542
Epoch 264/1000
971418/971418 [==============================] - 315s 324us/step - loss: 1.2809 - accuracy: 0.4584 - val_loss: 1.3018 - val_accuracy: 0.4540
Epoch 265/1000
971418/971418 [==============================] - 315s 324us/step - loss: 1.2808 - accuracy: 0.4581 - val_loss: 1.3025 - val_accuracy: 0.4540
Epoch 266/1000
971418/971418 [==============================] - 316s 325us/step

971418/971418 [==============================] - 308s 317us/step - loss: 1.2801 - accuracy: 0.4580 - val_loss: 1.3012 - val_accuracy: 0.4543
Epoch 313/1000
971418/971418 [==============================] - 308s 317us/step - loss: 1.2798 - accuracy: 0.4585 - val_loss: 1.3016 - val_accuracy: 0.4546
Epoch 314/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2800 - accuracy: 0.4581 - val_loss: 1.3018 - val_accuracy: 0.4541
Epoch 315/1000
971418/971418 [==============================] - 308s 318us/step - loss: 1.2797 - accuracy: 0.4581 - val_loss: 1.3019 - val_accuracy: 0.4545
Epoch 316/1000
971418/971418 [==============================] - 309s 318us/step - loss: 1.2801 - accuracy: 0.4585 - val_loss: 1.3020 - val_accuracy: 0.4543
Epoch 317/1000
971418/971418 [==============================] - 308s 317us/step - loss: 1.2804 - accuracy: 0.4582 - val_loss: 1.3018 - val_accuracy: 0.4542
Epoch 318/1000
971418/971418 [==============================] - 309s 318us/step

971418/971418 [==============================] - 307s 316us/step - loss: 1.2791 - accuracy: 0.4586 - val_loss: 1.3014 - val_accuracy: 0.4551
Epoch 365/1000
971418/971418 [==============================] - 306s 315us/step - loss: 1.2794 - accuracy: 0.4584 - val_loss: 1.3015 - val_accuracy: 0.4549
Epoch 366/1000
971418/971418 [==============================] - 305s 314us/step - loss: 1.2797 - accuracy: 0.4585 - val_loss: 1.3015 - val_accuracy: 0.4549
Epoch 367/1000
971418/971418 [==============================] - 306s 315us/step - loss: 1.2791 - accuracy: 0.4584 - val_loss: 1.3012 - val_accuracy: 0.4546
Epoch 368/1000
971418/971418 [==============================] - 310s 319us/step - loss: 1.2794 - accuracy: 0.4585 - val_loss: 1.3011 - val_accuracy: 0.4549
Epoch 369/1000
971418/971418 [==============================] - 301s 310us/step - loss: 1.2792 - accuracy: 0.4584 - val_loss: 1.3012 - val_accuracy: 0.4549
Epoch 370/1000
971418/971418 [==============================] - 294s 303us/step

In [ ]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'
import matplotlib.pyplot as plt


def plot_confusion_matrix(cm, labels, title='Confusion matrix', cmap=plt.cm.Blues):
    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(labels))
    plt.xticks(tick_marks, labels, rotation=45)
    plt.yticks(tick_marks, labels)
    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label')

In [ ]:
pred_train_y = model.predict(input_list_train)
pred_test_y = model.predict(input_list_test)

intermediate_train_vals = intermediate_model.predict(input_list_train)
intermediate_test_vals = intermediate_model.predict(input_list_test)

In [ ]:
from sklearn.metrics import accuracy_score
from keras.utils import to_categorical

train_class_labels = np.argmax(pred_train_y, axis=1)
train_class_vector_one_hot = to_categorical(train_class_labels)
train_class_actuals = np.argmax(y_train, axis=1)

test_class_labels = np.argmax(pred_test_y, axis=1)
test_class_vector_one_hot = to_categorical(test_class_labels)
test_class_actuals = np.argmax(y_test, axis=1)


print(accuracy_score(class_actuals, class_labels))

print(accuracy_score(test_class_actuals, test_class_labels))



In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix


print('Scoring validation')
score = accuracy_score(test_class_actuals, test_class_labels)
 
print('Accuracy:', score)

cm = confusion_matrix(test_class_actuals, test_class_labels)
np.set_printoptions(precision=2)
print('Confusion matrix, without normalization')
print(cm)
plt.figure()
plot_confusion_matrix(cm, bin_names, title='Confusion matrix')

# Normalize the confusion matrix by row (i.e by the number of samples in each class)
cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
print('Normalized confusion matrix')
print(cm_normalized)
plt.figure()
plot_confusion_matrix(cm_normalized, bin_names, title='Normalized confusion matrix')

print('Scoring backtest data')
score = accuracy_score(train_class_actuals, train_class_labels)
 
print('Accuracy:', score)

cm = confusion_matrix(train_class_actuals, train_class_labels)
np.set_printoptions(precision=2)
print('Confusion matrix, without normalization')
print(cm)
plt.figure()
plot_confusion_matrix(cm, bin_names, title='Confusion matrix')

# Normalize the confusion matrix by row (i.e by the number of samples in each class)
cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
print('Normalized confusion matrix')
print(cm_normalized)
plt.figure()
plot_confusion_matrix(cm_normalized, bin_names, title='Normalized confusion matrix')

In [ ]:
from sklearn.experimental import enable_hist_gradient_boosting
from sklearn.ensemble import RandomForestClassifier, HistGradientBoostingClassifier, VotingClassifier

histogram_model = HistGradientBoostingClassifier(
    max_iter=343, 
    max_leaf_nodes=623, 
    learning_rate=0.1, 
    min_samples_leaf=2, 
    l2_regularization=0.,
    verbose=1
)
    
print('-' * 50)
print('Fitting histogram model')
histogram_model.fit(intermediate_train_vals, train_class_actuals)
print('-' * 50)
print('Histogram model done')

hist_train_pred_y = histogram_model.predict(intermediate_train_vals)
hist_test_pred_y = histogram_model.predict(intermediate_test_vals)



In [ ]:
print('Scoring validation')
pred_class_labels = hist_test_pred_y
score = accuracy_score(test_class_actuals, pred_class_labels)
 
print('Accuracy:', score)

cm = confusion_matrix(test_class_actuals, pred_class_labels)
np.set_printoptions(precision=2)
print('Confusion matrix, without normalization')
print(cm)
plt.figure()
plot_confusion_matrix(cm, bin_names, title='Confusion matrix')

# Normalize the confusion matrix by row (i.e by the number of samples in each class)
cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
print('Normalized confusion matrix')
print(cm_normalized)
plt.figure()
plot_confusion_matrix(cm_normalized, bin_names, title='Normalized confusion matrix')


print('Scoring backtest')
pred_class_labels = hist_train_pred_y
score = accuracy_score(train_class_actuals, pred_class_labels)
 
print('Accuracy:', score)

cm = confusion_matrix(train_class_actuals, pred_class_labels)
np.set_printoptions(precision=2)
print('Confusion matrix, without normalization')
print(cm)
plt.figure()
plot_confusion_matrix(cm, bin_names, title='Confusion matrix')

# Normalize the confusion matrix by row (i.e by the number of samples in each class)
cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
print('Normalized confusion matrix')
print(cm_normalized)
plt.figure()
plot_confusion_matrix(cm_normalized, bin_names, title='Normalized confusion matrix')


In [ ]:
from sklearn.ensemble import RandomForestClassifier

random_forest_model =  RandomForestClassifier(
         max_depth=20, n_estimators=505, min_samples_split=2, min_samples_leaf=1
)

print('-' * 50)
print('Fitting random forest model')
random_forest_model.fit(intermediate_vals, class_actuals)
print('-' * 50)
print('Random forest done')

train_pred_y = random_forest_model.predict(intermediate_vals)

print('Scoring')
pred_class_labels = train_pred_y
score = accuracy_score(class_actuals, pred_class_labels)
 
print('Accuracy:', score)

cm = confusion_matrix(class_actuals, pred_class_labels)
np.set_printoptions(precision=2)
print('Confusion matrix, without normalization')
print(cm)
plt.figure()
plot_confusion_matrix(cm, bin_names, title='Confusion matrix')

# Normalize the confusion matrix by row (i.e by the number of samples in each class)
cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
print('Normalized confusion matrix')
print(cm_normalized)
plt.figure()
plot_confusion_matrix(cm_normalized, bin_names, title='Normalized confusion matrix')

In [ ]:
from mlxtend.classifier import EnsembleVoteClassifier

voting_model = EnsembleVoteClassifier(
    clfs=[random_forest_model, histogram_model], 
    voting='soft',
    refit=False,
    verbose=1)

print('Fitting voting classifier')
voting_model.fit(intermediate_vals, class_actuals)
print('-' * 50)
print('Voting classifier done')

train_pred_y = voting_model.predict(intermediate_vals)

print('Scoring')
pred_class_labels = train_pred_y
score = accuracy_score(class_actuals, pred_class_labels)
 
print('Accuracy:', score)

cm = confusion_matrix(class_actuals, pred_class_labels)
np.set_printoptions(precision=2)
print('Confusion matrix, without normalization')
print(cm)
plt.figure()
plot_confusion_matrix(cm, bin_names, title='Confusion matrix')

# Normalize the confusion matrix by row (i.e by the number of samples in each class)
cm_normalized = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
print('Normalized confusion matrix')
print(cm_normalized)
plt.figure()
plot_confusion_matrix(cm_normalized, bin_names, title='Normalized confusion matrix')
